## Scraping Competitor Data

### Who are Hailr's competitors?

- **Locally:**
    - Uwina (https://uwina.com/)
    - Inner Reality (https://innereality.com/)
    - Smaller Bespoke Service Agencies

- **Internationally:**
    - Playable (https://playable.com/)
    - Oddicci (https://odicci.com/)
    - Ceros (https://www.ceros.com/)
    - Brame (https://brame.io/)
    - Jebbit 

### Who is Hailr's target audience?

- **Buyer Target Audience:**
  - Professionals in Advertising, Media, and Customer Engagement
  - Members of Loyalty, Marketing Team, and Data Team
  - Individuals with control over budget
  - Involved in legal and procurement approval processes
  - middle market manager at brands

- **User Target Audience:**
  - Consumers of brands
  - Individuals interested in earning rewards for their time and attention
  - Those wanting to interact with branded content and earn rewards
  - Users seeking access to gamified campaigns on the platform

### Brands or businesses Hailr can align with 

- Disney
- National Geographic
- KFC
- Shell
- Sasol
- Spur
- Click's
- TFG
- Food Lover's Market
- Distell
- Savanna
- Makro
- Ackermans
- Rand Merchant Bank (RMB)
- Student Village
- Johnson & Johnson

# Code

In [1]:
%pip install plotly
%pip install --upgrade nbformat
%pip install statsmodels

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


So how I've done this is that I've input the competitor company website into Google Keyword planner and then downloaded the relevent keywords.

### Class with functions for analysis

In [2]:
# KeywordAnalyzer class

class KeywordAnalyzer:
    def __init__(self, df):
        self.df = df
    # Returns DF with the selected keyword
    def target_keyword(self, target_word):
        df_new = self.df[self.df['Keyword'].str.contains(target_word, case=False)].reset_index(drop=True)
        return df_new
    
    # Returns DF with the average monthly searches: bigger, smaller, or equal to 
    def avg_monthly_searches(self, num_searches, comparitor):
        if comparitor == 'bigger':
            df_new = self.df[self.df['Avg. monthly searches'] > num_searches].reset_index(drop=True)
        elif comparitor == 'smaller':
            df_new = self.df[self.df['Avg. monthly searches'] < num_searches].reset_index(drop=True)
        else:
            df_new = self.df[self.df['Avg. monthly searches'] == num_searches].reset_index(drop=True)
        return df_new
    
    # Returns DF with competiveness ratio: bigger, smaller, or equal to  
    def competiveness_ratio(self, ratio, comparitor):
        if comparitor == 'bigger':
            df_new = self.df[self.df['Competitiveness Ratio'] > ratio].reset_index(drop=True)
        elif comparitor == 'smaller':
            df_new = self.df[self.df['Competitiveness Ratio'] < ratio].reset_index(drop=True)
        else:
            df_new = self.df[self.df['Competitiveness Ratio'] == ratio].reset_index(drop=True)
        return df_new
    

### Reading in DFs of competitors keyword planner

In [36]:
import os
import pandas as pd

# Specify the folder path
folder_path = '/Users/matthewrosenthal/Desktop/SEO Report'

# Initialize an empty dictionary to store DataFrames
dfs = {}

# Iterate over each file in the folder
for file_name in os.listdir(folder_path):
    if file_name.endswith('.xlsx'):
        # Construct the full path to the file
        file_path = os.path.join(folder_path, file_name)
        
        # Read the Excel file into a DataFrame
        df_name = os.path.splitext(file_name)[0]  # Extract DataFrame name from file name
        dfs[df_name] = pd.read_excel(file_path)

# Now, the 'dfs' dictionary contains DataFrames with keys as file names (without extension)
# Example usage:
# dfs['playable']  # Access the DataFrame from the first file
# dfs['brame']  # Access the DataFrame from the second file
# ...

# If you want to work with all DataFrames collectively, you can concatenate them into a single DataFrame:
combined_df = pd.concat(dfs.values(), axis=0, ignore_index=True)

In [56]:
# dfs['odicci_nigeria_oct']

### Check-in and initial analysis: what is interesting here and what can we use?

First things first is to define the goal of this report:

- Understand competitors keywords
    - Try and understand competitors strategies and the effectiveness of certain keywords
    - Can define a metric here that is cost of keyword over click rate?
- Reccomend keywords for Hailr
    - Focus on keywords related to advertising, media, customer engagement, and brand loyalty 
    - Long-tail keywords: what is Hailr's unique product offering? Games, rewards, playable, challanges, fun, engagement
- How to target brand managers? 
    - This is more geared to LinkedIn research and less Keyword Planner
    - Look into potential customers and think how to target brand managers
    - LinkedIn advertising 
    - Create campaigns that target the brands we are interested in working with 
- Determing keyword costs
    - This will come hand-in-hand with the metric that divides cost of bid by average number of clicks

### Competitiveness Ratio (CR)


CR = competition(index value)/avg bidding price

- This ratio gives rise to 3 different strategies :
    1. Higher ratio is better 
    2. Lower ratio is better (cost conscious)
    3. Balanced approach 

In [38]:
# Function to calculate Competitiveness Ratio
def calculate_competitiveness_ratio(df):
    # Calculate average bid price
    df['Avg. Bid Price'] = (df['Top of page bid (low range)'] + df['Top of page bid (high range)']) / 2
    # Calculate Competitiveness Ratio
    df['Competitiveness Ratio'] = df['Competition (indexed value)'] / df['Avg. Bid Price']
    return df


In [39]:
# Iterate through each DataFrame in the dictionary
for df_name, df in dfs.items():
    # Call the function to calculate and add Competitiveness Ratio
    dfs[df_name] = calculate_competitiveness_ratio(df)

### Full Keyword Analyser 

#### Code

In [40]:
import pandas as pd
import plotly.express as px

class KeywordAnalyzer:
    def __init__(self, dataframe):
        self.dataframe = dataframe

    def target_keyword(self, target_word):
        return self.dataframe[self.dataframe['Keyword'].str.contains(target_word, case=False)].reset_index(drop=True)

    def avg_monthly_searches(self, num_searches, comparitor):
        if comparitor == 'bigger':
            return self.dataframe[self.dataframe['Avg. monthly searches'] > num_searches].reset_index(drop=True)
        elif comparitor == 'smaller':
            return self.dataframe[self.dataframe['Avg. monthly searches'] < num_searches].reset_index(drop=True)
        else:
            return self.dataframe[self.dataframe['Avg. monthly searches'] == num_searches].reset_index(drop=True)

    def competitiveness_ratio(self, threshold, comparitor):
        if comparitor == 'bigger':
            return self.dataframe[self.dataframe['Competition (indexed value)'] / self.dataframe['Avg. Bid Price'] > threshold].reset_index(drop=True)
        elif comparitor == 'smaller':
            return self.dataframe[self.dataframe['Competition (indexed value)'] / self.dataframe['Avg. Bid Price'] < threshold].reset_index(drop=True)
        else:
            return self.dataframe[self.dataframe['Competition (indexed value)'] / self.dataframe['Avg. Bid Price'] == threshold].reset_index(drop=True)

    def create_scatter_plot(self, title='', save_path=None):
        # Create a scatter plot with hover information and linear regression line
        fig = px.scatter(self.dataframe, x='Avg. Bid Price', y='Competition (indexed value)', 
                         custom_data=['Keyword', 'Avg. monthly searches'], 
                         color='Avg. monthly searches',  # Color points based on 'Avg. monthly searches'
                        #  color_continuous_scale=['blue', 'green', 'red', 'pink'],
                        #  size='Avg. monthly searches',
                         labels={'X': 'Avg. Bid Price', 'Y': 'Competition (indexed value)'}, title=title)

        # Customize hover information
        fig.update_traces(textposition='top center', hovertemplate='Keyword: %{customdata[0]}<br>Avg. Bid Price: %{x}<br>Competition (indexed value): %{y}<br>Avg. monthly searches: %{customdata[1]}')

        if save_path:
            fig.write_html(save_path)

        # Show the plot
        fig.show()

# Example usage:
# instance_of_your_class.create_scatter_plot(title='Your Title', save_path='path/to/save_plot.html')

    def create_custom_scatter_plot(self, dataframe=None, title='', save_path=None):
        # Use the specified DataFrame or default to the class DataFrame
        dataframe = dataframe if dataframe is not None else self.dataframe

        # Create a scatter plot with hover information
        fig = px.scatter(dataframe, x='Avg. Bid Price', y='Competition (indexed value)', custom_data=['Keyword'], labels={'X': 'Avg. Bid Price', 'Y': 'Competition (indexed value)'}, title=title)

        # Customize hover information
        fig.update_traces(textposition='top center', hovertemplate='Keyword: %{customdata[0]}<br>Avg. Bid Price: %{x}<br>Competition (indexed value): %{y}')
        fig.update_layout(showlegend=False)  # If you don't want a legend for the trendline

        if save_path:
            fig.write_html(save_path)

        # Show the plot
        fig.show()
    
    def create_3_month_scatter_plot(self, title='', save_path=None):
        # Create a scatter plot with hover information and linear regression line
        fig = px.scatter(self.dataframe, x='Avg. Bid Price', y='Three month change', 
                         custom_data=['Keyword', 'Avg. monthly searches'], 
                         color='Avg. monthly searches',  # Color points based on 'Avg. monthly searches'
                        #  color_continuous_scale=['blue', 'green', 'red', 'pink'],
                        #  size='Avg. monthly searches',
                         labels={'X': 'Avg. Bid Price', 'Y': 'Three month change'}, title=title)

        # Customize hover information
        fig.update_traces(textposition='top center', hovertemplate='Keyword: %{customdata[0]}<br>Avg. Bid Price: %{x}<br>Three month change: %{y}<br>Avg. monthly searches: %{customdata[1]}')

        if save_path:
            fig.write_html(save_path)

        # Show the plot
        fig.show()
    
    

In [57]:
def analyze_company(company_name, target_keyword):
    # Assuming dfs is a DataFrame with a column named 'company_name'
    brame = dfs[company_name]
    keyword_analyzer = KeywordAnalyzer(brame)

    keyword_analyzer.create_scatter_plot(title=f'{company_name} Full Keyword Scatter Plot')
    # keyword_analyzer.create_3_month_scatter_plot(title='3 Month Scatter Plot')

    marketing_keyword = keyword_analyzer.target_keyword(target_keyword)

    print('The number of words that contain "{}" is {}'.format(target_keyword, len(marketing_keyword)))

    # keyword_analyzer.create_scatter_plot(title='Full Keyword Scatter Plot')

    more_than_50_tw_marketing = KeywordAnalyzer(marketing_keyword).avg_monthly_searches(50, 'bigger')

    print('The number of words that contain "{}" and get more than 50 searches is {}'.format(target_keyword, len(more_than_50_tw_marketing)))

    if len(marketing_keyword) == 0:
        print('No words with "{}"'.format(target_keyword))
    else:
        percent_more_than_50 = round(len(more_than_50_tw_marketing) / len(marketing_keyword) * 100, 2)
        print('The percentage of words that contain "{}" and get more than 50 searches is {}%'.format(target_keyword, percent_more_than_50))

    # keyword_analyzer = KeywordAnalyzer(more_than_50_tw_marketing)
    keyword_analyzer = KeywordAnalyzer(marketing_keyword)

    display(marketing_keyword)

    keyword_analyzer.create_scatter_plot(title='Target Keyword "{}" Scatter Plot'.format(target_keyword))

    more_than_500_tw_marketing = KeywordAnalyzer(marketing_keyword).avg_monthly_searches(500, 'bigger')

    print('The number of words that contain "{}" and get more than 500 searches is {}'.format(target_keyword, len(more_than_500_tw_marketing)))

    print('These words are:')
    display(more_than_500_tw_marketing)


In [60]:
def analyze_company(company_name, target_keyword, save_path):
    # Assuming dfs is a DataFrame with a column named 'company_name'
    brame = dfs[company_name]
    keyword_analyzer = KeywordAnalyzer(brame)
    # print(brame.columns)

    # Create the scatter plot for the entire dataset
    keyword_analyzer.create_scatter_plot(title=f'Full Keyword Scatter Plot {company_name}', save_path=save_path)

    # Target specific keywords
    marketing_keyword = keyword_analyzer.target_keyword(target_keyword)

    # print('The number of words that contain "{}" is {}'.format(target_keyword, len(marketing_keyword)))

    # if len(marketing_keyword) == 0:
        # print('No words with "{}"'.format(target_keyword))
    # else:
        # Analyze keywords with more than 50 searches
        # more_than_50_tw_marketing = keyword_analyzer.avg_monthly_searches(50, 'bigger')

        # print('The number of words that contain "{}" and get more than 50 searches is {}'.format(target_keyword, len(more_than_50_tw_marketing)))

        # percent_more_than_50 = round(len(more_than_50_tw_marketing) / len(marketing_keyword) * 100, 2)
        # print('The percentage of words that contain "{}" and get more than 50 searches is {}%'.format(target_keyword, percent_more_than_50))

        # Display and create scatter plot for the target keyword
        # display(marketing_keyword)
        # keyword_analyzer.create_scatter_plot(title='Target Keyword "{}" Scatter Plot'.format(target_keyword))

        # Analyze keywords with more than 500 searches
        # more_than_500_tw_marketing = keyword_analyzer.avg_monthly_searches(500, 'bigger')

        # print('The number of words that contain "{}" and get more than 500 searches is {}'.format(target_keyword, len(more_than_500_tw_marketing)))

        # print('These words are:')
        # display(more_than_500_tw_marketing)


In [63]:
dfs.keys()

dict_keys(['odicci_nigeria_oct', 'ceros_uk_oct', 'jebbit_ireland_oct', 'ceros_sa_oct', 'jebbit_nigeria_oct', 'odicci_ireland_oct', 'brame_nigera_oct', 'inner_reality_nigeria_oct', 'ceros_nigeria_oct', 'brame_ireland_oct', 'inner_reality_ireland_oct', 'ceros_ireland_oct', 'brame_sa_oct', 'odicci_uk_oct', 'jebbit_uk_oct', 'inner_reality_sa_oct', 'playable_ireland_oct', 'playable_sa_oct', 'playable_uk_oct', 'inner_reality_uk_oct', 'jebbit_sa_oct', 'brame_uk_oct', 'odicci_sa_oct', 'playable_nigeria_oct'])

In [65]:
for company_name in dfs.keys():
    company_name_input = company_name
    target_keyword_input = 'gamification'
    save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"
    analyze_company(company_name_input, target_keyword_input, save_path)


#### Brame

In [61]:
company_name_input = 'brame_sa_oct'
target_keyword_input = 'gamification'
save_path = "/Users/matthewrosenthal/Desktop/Plots for SEO/brame_sa_oct.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Gam

In [40]:
company_name_input = 'brame_sa_oct'
target_keyword_input = 'gam'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "gam" is 55
The number of words that contain "gam" and get more than 50 searches is 0
The percentage of words that contain "gam" and get more than 50 searches is 0.0%


Keyword Currency  Avg. monthly searches  \
0                 gamification marketing      ZAR                   50.0   
1        gamification marketing platform      ZAR                    0.0   
2                     brame gamification      ZAR                   50.0   
3                 gamification solutions      ZAR                   50.0   
4                  customer gamification      ZAR                   50.0   
5                  gamification products      ZAR                   50.0   
6                         game marketing      ZAR                   50.0   
7             gamification and marketing      ZAR                   50.0   
8                  gamification campaign      ZAR                   50.0   
9            gamification in advertising      ZAR                   50.0   
10      gamification marketing campaigns      ZAR                    0.0   
11  gamification for customer engagement      ZAR                   50.0   
12                gamification in retail      ZAR                   50.0   
13                       games marketing      ZAR                   50.0   
14   gamification to increase engagement      ZAR                    0.0   
15          gamification email marketing      ZAR                    0.0   
16           gamification and engagement      ZAR                   50.0   
17             social media gamification      ZAR                   50.0   
18               gamification engagement      ZAR                   50.0   
19       interactive games for customers      ZAR                    0.0   
20                    brand gamification      ZAR                   50.0   
21                    email gamification      ZAR                    0.0   
22         marketing games for customers      ZAR                    0.0   
23                   gamification emails      ZAR                    0.0   
24                  digital gamification      ZAR                   50.0   
25          gamification lead generation      ZAR                    0.0   
26        gamification digital marketing      ZAR                   50.0   
27   gamification social media marketing      ZAR                    0.0   
28              gamification in industry      ZAR                    0.0   
29      gamification increase engagement      ZAR                    0.0   
30                 in store gamification      ZAR                    0.0   
31                   marketing your game      ZAR                    0.0   
32     gamification marketing case study      ZAR                    0.0   
33          gamification success stories      ZAR                    0.0   
34                 gamification industry      ZAR                    0.0   
35               gamification experience      ZAR                   50.0   
36                     data gamification      ZAR                   50.0   
37                      a game marketing      ZAR                    0.0   
38           best gamification campaigns      ZAR                    0.0   
39               case study gamification      ZAR                   50.0   
40                   games for customers      ZAR                    0.0   
41                     gamification case      ZAR                    0.0   
42                  gamification content      ZAR                   50.0   
43                   gamification growth      ZAR                    0.0   
44                gamification in emails      ZAR                    0.0   
45         gamification in retail stores      ZAR                    0.0   
46                 gamification in store      ZAR                    0.0   
47     gamification marketing statistics      ZAR                    0.0   
48                   gamification models      ZAR                   50.0   
49                      gamification now      ZAR                    NaN   
50               gamification of content      ZAR                   50.0   
51          gamification on social media      ZAR                   50.0   
52   

The number of words that contain "gam" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

###### Interactive

In [41]:
company_name_input = 'brame_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "interactive" is 16
The number of words that contain "interactive" and get more than 50 searches is 0
The percentage of words that contain "interactive" and get more than 50 searches is 0.0%


Keyword Currency  \
0                      interactive advertising      ZAR   
1                        interactive marketing      ZAR   
2                        interactive campaigns      ZAR   
3              interactive games for customers      ZAR   
4                        interactive platforms      ZAR   
5              interactive marketing campaigns      ZAR   
6                         interactive branding      ZAR   
7                         interactive features      ZAR   
8                          interactive product      ZAR   
9                              cpg interactive      ZAR   
10               interactive digital campaigns      ZAR   
11               interactive digital platforms      ZAR   
12                          interactive market      ZAR   
13  interactive marketing in service marketing      ZAR   
14                    interactive marketing is      ZAR   
15                             interactive top      ZAR   

    Avg. monthly searches Three month change YoY change Competition  \
0                    50.0                  0          0         Low   
1                    50.0                  0       -0.9         Low   
2                    50.0                  0          0         Low   
3                     0.0                  0         -1     Unknown   
4                    50.0                  0          0         Low   
5                    50.0                  0          0         Low   
6                    50.0                  0          0         Low   
7                    50.0                  0          0         Low   
8                    50.0                  0          0         Low   
9                     0.0                  0          0     Unknown   
10                    0.0                  0          0     Unknown   
11                   50.0                  0          0         Low   
12                   50.0                  0          0         Low   
13                    0.0                  0          0     Unknown   
14                    0.0                  0         -1     Unknown   
15                    0.0                  0          0     Unknown   

    Competition (indexed value)  Top of page bid (low range)  \
0                           5.0                        24.12   
1                           0.0                          NaN   
2                           0.0                          NaN   
3                           NaN                          NaN   
4                           0.0                          NaN   
5                          19.0                          NaN   
6                           0.0                          NaN   
7                           0.0                          NaN   
8                           0.0                          NaN   
9                           NaN                          NaN   
10                          NaN                          NaN   
11                          0.0                          NaN   
12                         17.0                          NaN   
13                          NaN                          NaN   
14                          NaN                          NaN   
15                          NaN                          NaN   

    Top of page bid (high range)  Avg. Bid Price  Competitiveness Ratio  
0                          57.43          40.775               0.122624  
1                            NaN             NaN                    NaN  
2                            NaN             NaN                    NaN  
3                            NaN             NaN                    NaN  
4                            NaN             NaN                    NaN  
5                            NaN             NaN                    NaN  
6                            NaN             NaN                    NaN  
7                            NaN             NaN                    NaN  
8                            NaN             NaN                    NaN 

The number of words that contain "interactive" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

#### Playable

##### Gam

In [51]:

company_name_input = 'playable_sa_oct'
target_keyword_input = 'gam'
save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Interactive

In [15]:
company_name_input = 'playable_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

ValueError: Value of 'x' is not the name of a column in 'data_frame'. Expected one of ['Keyword', 'Currency', 'Avg. monthly searches', 'Three month change', 'YoY change', 'Competition', 'Competition (indexed value)', 'Top of page bid (low range)', 'Top of page bid (high range)'] but received: Avg. Bid Price

#### Inner Reality

##### Gam

In [52]:
company_name_input = 'inner_reality_sa_oct'
target_keyword_input = 'gam'
save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Interactive

In [45]:
company_name_input = 'inner_reality_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "interactive" is 0
The number of words that contain "interactive" and get more than 50 searches is 0
No words with "interactive"


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

The number of words that contain "interactive" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

#### Odicci

##### Gam

In [53]:
company_name_input = 'odicci_sa_oct'
target_keyword_input = 'gam'
save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Interactive

In [47]:
company_name_input = 'odicci_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "interactive" is 20
The number of words that contain "interactive" and get more than 50 searches is 0
The percentage of words that contain "interactive" and get more than 50 searches is 0.0%


Keyword Currency  Avg. monthly searches  \
0            interactive content platform      ZAR                    0.0   
1                   interactive marketing      ZAR                   50.0   
2            interactive content software      ZAR                   50.0   
3         interactive games for customers      ZAR                    0.0   
4   interactive content creation software      ZAR                    0.0   
5            interactive customer journey      ZAR                    0.0   
6         interactive customer experience      ZAR                    0.0   
7                    interactive branding      ZAR                   50.0   
8                          interactive ad      ZAR                   50.0   
9                      interactive market      ZAR                   50.0   
10               interactive marketing is      ZAR                    0.0   
11    interactive marketing communication      ZAR                    0.0   
12                    interactive rewards      ZAR                    0.0   
13          interactive marketing example      ZAR                   50.0   
14          apa itu interactive marketing      ZAR                    NaN   
15         interactive marketing benefits      ZAR                   50.0   
16           interactive online marketing      ZAR                    0.0   
17         interactive marketing strategy      ZAR                   50.0   
18                      interactive sales      ZAR                    0.0   
19          interactive marketing company      ZAR                   50.0   

   Three month change YoY change Competition  Competition (indexed value)  \
0                   0         -1     Unknown                          NaN   
1                   0       -0.9         Low                          0.0   
2                   ∞          0      Medium                         33.0   
3                   0         -1     Unknown                          NaN   
4                   0          0     Unknown                          NaN   
5                   0          0     Unknown                          NaN   
6                   0          0     Unknown                          NaN   
7                   0          0         Low                          0.0   
8                   0          0         Low                          5.0   
9                   0          0         Low                         17.0   
10                  0         -1     Unknown                          NaN   
11                 -1         -1     Unknown                          NaN   
12                  0          0     Unknown                          NaN   
13                  0          0         Low                          0.0   
14                 --         --     Unknown                          NaN   
15                  0          0         Low                          0.0   
16                  0          0     Unknown                          NaN   
17                  0          0         Low                          0.0   
18                  0          0     Unknown                          NaN   
19                  ∞          ∞         Low                          0.0   

    Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                           NaN                           NaN             NaN   
1                           NaN                           NaN             NaN   
2                           NaN                           NaN             NaN   
3                           NaN                           NaN             NaN   
4                           NaN                           NaN             NaN   
5                           NaN                           NaN             NaN   
6                           NaN                           NaN             NaN   
7                           NaN                           NaN             NaN   
8                         24.12                         57.42        

The number of words that contain "interactive" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

#### Jebbit

##### Gam

In [54]:
company_name_input = 'jebbit_sa_oct'
target_keyword_input = 'gam'
save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Interactive 

In [48]:
company_name_input = 'jebbit_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "interactive" is 0
The number of words that contain "interactive" and get more than 50 searches is 0
No words with "interactive"


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

The number of words that contain "interactive" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

#### Ceros

##### Gam

In [55]:
company_name_input = 'ceros_sa_oct'
target_keyword_input = 'gam'
save_path = f"/Users/matthewrosenthal/Desktop/Plots for SEO/{company_name_input}.html"

analyze_company(company_name_input, target_keyword_input, save_path)

##### Interactive

In [50]:
company_name_input = 'ceros_sa_oct'
target_keyword_input = 'interactive'

analyze_company(company_name_input, target_keyword_input)

The number of words that contain "interactive" is 4
The number of words that contain "interactive" and get more than 50 searches is 0
The percentage of words that contain "interactive" and get more than 50 searches is 0.0%


Keyword Currency  Avg. monthly searches  \
0   interactive content platform      ZAR                    0.0   
1              ceros interactive      ZAR                    0.0   
2     create interactive content      ZAR                    0.0   
3  interactive content marketing      ZAR                   50.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                  0         -1     Unknown                          NaN   
1                  0          0     Unknown                          NaN   
2                 -1         -1     Unknown                          NaN   
3                  0          0         Low                          0.0   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   
1                          NaN                           NaN             NaN   
2                          NaN                           NaN             NaN   
3                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN  
1                    NaN  
2                    NaN  
3                    NaN

The number of words that contain "interactive" and get more than 500 searches is 0
These words are:


Empty DataFrame
Columns: [Keyword, Currency, Avg. monthly searches, Three month change, YoY change, Competition, Competition (indexed value), Top of page bid (low range), Top of page bid (high range), Avg. Bid Price, Competitiveness Ratio]
Index: []

### Interesting Keywords

#### Coded

In [55]:
interesting_keywords = ['advertising games', 'branded games', 'create interactive content', 'gamification', 
                        'interative advertising', 'interactive content', 'marketing games']

In [89]:
def analyze_interesting_keywords(company_name, interesting_keywords, display_df):
    # Assuming dfs is a DataFrame with a column named 'company_name'
    brame = dfs[company_name]
    keyword_analyzer = KeywordAnalyzer(brame)

    for words in interesting_keywords:

        marketing_keyword = keyword_analyzer.target_keyword(words)

        print('The number of words that contain "{}" is {}'.format(words, len(marketing_keyword)))

        if display_df == True:

            if len(marketing_keyword) > 0:
                display(marketing_keyword)
        
        else:
            continue

    
    # # keyword_analyzer = KeywordAnalyzer(more_than_50_tw_marketing)
    # keyword_analyzer = KeywordAnalyzer(marketing_keyword)

    # display(marketing_keyword)

    # keyword_analyzer.create_scatter_plot(title='Target Keyword "{}" Scatter Plot'.format(target_keyword))

    # more_than_500_tw_marketing = KeywordAnalyzer(marketing_keyword).avg_monthly_searches(500, 'bigger')

    # print('The number of words that contain "{}" and get more than 500 searches is {}'.format(target_keyword, len(more_than_500_tw_marketing)))

    # print('These words are:')
    # display(more_than_500_tw_marketing)

#### Implementation

In [90]:
company_name = 'brame_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords, True)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 48


Keyword Currency  Avg. monthly searches  \
0                 gamification marketing      ZAR                   50.0   
1        gamification marketing platform      ZAR                    0.0   
2                     brame gamification      ZAR                   50.0   
3                 gamification solutions      ZAR                   50.0   
4                  customer gamification      ZAR                   50.0   
5                  gamification products      ZAR                   50.0   
6             gamification and marketing      ZAR                   50.0   
7                  gamification campaign      ZAR                   50.0   
8            gamification in advertising      ZAR                   50.0   
9       gamification marketing campaigns      ZAR                    0.0   
10  gamification for customer engagement      ZAR                   50.0   
11                gamification in retail      ZAR                   50.0   
12   gamification to increase engagement      ZAR                    0.0   
13          gamification email marketing      ZAR                    0.0   
14           gamification and engagement      ZAR                   50.0   
15             social media gamification      ZAR                   50.0   
16               gamification engagement      ZAR                   50.0   
17                    brand gamification      ZAR                   50.0   
18                    email gamification      ZAR                    0.0   
19                   gamification emails      ZAR                    0.0   
20                  digital gamification      ZAR                   50.0   
21          gamification lead generation      ZAR                    0.0   
22        gamification digital marketing      ZAR                   50.0   
23   gamification social media marketing      ZAR                    0.0   
24              gamification in industry      ZAR                    0.0   
25      gamification increase engagement      ZAR                    0.0   
26                 in store gamification      ZAR                    0.0   
27     gamification marketing case study      ZAR                    0.0   
28          gamification success stories      ZAR                    0.0   
29                 gamification industry      ZAR                    0.0   
30               gamification experience      ZAR                   50.0   
31                     data gamification      ZAR                   50.0   
32           best gamification campaigns      ZAR                    0.0   
33               case study gamification      ZAR                   50.0   
34                     gamification case      ZAR                    0.0   
35                  gamification content      ZAR                   50.0   
36                   gamification growth      ZAR                    0.0   
37                gamification in emails      ZAR                    0.0   
38         gamification in retail stores      ZAR                    0.0   
39                 gamification in store      ZAR                    0.0   
40     gamification marketing statistics      ZAR                    0.0   
41                   gamification models      ZAR                   50.0   
42                      gamification now      ZAR                    NaN   
43               gamification of content      ZAR                   50.0   
44          gamification on social media      ZAR                   50.0   
45                  gamification pricing      ZAR                    0.0   
46                insurance gamification      ZAR                   50.0   
47               successful gamification      ZAR                    0.0   

   Three month change YoY change Competition  Competition (indexed value)  \
0                   0          0         Low                          8.0   
1                   0          0     Unknown                          NaN   
2                   ∞          ∞         Low                         14.0   


The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 1


Keyword Currency  Avg. monthly searches  \
0  marketing games for customers      ZAR                    0.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                 -1         -1     Unknown                          NaN   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN

In [61]:
company_name = 'playable_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 3


Keyword Currency  Avg. monthly searches Three month change  \
0           branded games      ZAR                   50.0                  0   
1   company branded games      ZAR                    NaN                 --   
2  branded games examples      ZAR                    0.0                  0   

  YoY change Competition  Competition (indexed value)  \
0          0         Low                         32.0   
1         --     Unknown                          NaN   
2         -1     Unknown                          NaN   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   
1                          NaN                           NaN             NaN   
2                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN  
1                    NaN  
2                    NaN

The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 64


Keyword Currency  Avg. monthly searches  \
0                 gamification marketing      ZAR                   50.0   
1        gamification marketing platform      ZAR                    0.0   
2                      gamification saas      ZAR                    0.0   
3   gamification for customer engagement      ZAR                   50.0   
4                       gamification api      ZAR                   50.0   
..                                   ...      ...                    ...   
59                     data gamification      ZAR                   50.0   
60              gamification market size      ZAR                    0.0   
61       different types of gamification      ZAR                   50.0   
62                 types of gamification      ZAR                   50.0   
63         gamification marketing agency      ZAR                    0.0   

   Three month change YoY change Competition  Competition (indexed value)  \
0                   0          0         Low                          8.0   
1                   0          0     Unknown                          NaN   
2                   0          0     Unknown                          NaN   
3                   ∞          0         Low                          0.0   
4                   ∞          0      Medium                         43.0   
..                ...        ...         ...                          ...   
59                  ∞          ∞         Low                          0.0   
60                  0         -1     Unknown                          NaN   
61                  ∞          0         Low                          0.0   
62                  0          0         Low                          0.0   
63                  0          0     Unknown                          NaN   

    Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                           NaN                           NaN             NaN   
1                           NaN                           NaN             NaN   
2                           NaN                           NaN             NaN   
3                           NaN                           NaN             NaN   
4                           NaN                           NaN             NaN   
..                          ...                           ...             ...   
59                          NaN                           NaN             NaN   
60                          NaN                           NaN             NaN   
61                          NaN                           NaN             NaN   
62                          NaN                           NaN             NaN   
63                          NaN                           NaN             NaN   

    Competitiveness Ratio  
0                     NaN  
1                     NaN  
2                     NaN  
3                     NaN  
4                     NaN  
..                    ...  
59                    NaN  
60                    NaN  
61                    NaN  
62                    NaN  
63                    NaN  

[64 rows x 11 columns]

The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 10


Keyword Currency  Avg. monthly searches  \
0                       marketing games      ZAR                   50.0   
1               digital marketing games      ZAR                    0.0   
2         marketing games for customers      ZAR                    0.0   
3                online marketing games      ZAR                   50.0   
4           interactive marketing games      ZAR                   50.0   
5      fun marketing games for students      ZAR                    0.0   
6  digital marketing games for students      ZAR                    0.0   
7                   fun marketing games      ZAR                    0.0   
8               marketing games to play      ZAR                    0.0   
9   online marketing games for students      ZAR                    0.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                  0          0         Low                          7.0   
1                 -1         -1     Unknown                          NaN   
2                 -1         -1     Unknown                          NaN   
3                  ∞          ∞      Medium                         33.0   
4                  0          ∞         Low                          0.0   
5                  0         -1     Unknown                          NaN   
6                  0          0     Unknown                          NaN   
7                  0         -1     Unknown                          NaN   
8                 -1          0     Unknown                          NaN   
9                  0          0     Unknown                          NaN   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                         7.15                         32.89           20.02   
1                          NaN                           NaN             NaN   
2                          NaN                           NaN             NaN   
3                          NaN                           NaN             NaN   
4                          NaN                           NaN             NaN   
5                          NaN                           NaN             NaN   
6                          NaN                           NaN             NaN   
7                          NaN                           NaN             NaN   
8                          NaN                           NaN             NaN   
9                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                0.34965  
1                    NaN  
2                    NaN  
3                    NaN  
4                    NaN  
5                    NaN  
6                    NaN  
7                    NaN  
8                    NaN  
9                    NaN

In [62]:
company_name = 'jebbit_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 0


In [63]:
company_name = 'inner_reality_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 0


In [64]:
company_name = 'odicci_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 3


Keyword Currency  Avg. monthly searches  \
0           interactive content platform      ZAR                    0.0   
1           interactive content software      ZAR                   50.0   
2  interactive content creation software      ZAR                    0.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                  0         -1     Unknown                          NaN   
1                  ∞          0      Medium                         33.0   
2                  0          0     Unknown                          NaN   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   
1                          NaN                           NaN             NaN   
2                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN  
1                    NaN  
2                    NaN

The number of words that contain "marketing games" is 0


In [65]:
company_name = 'ceros_sa_oct'

analyze_interesting_keywords(company_name, interesting_keywords)

The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 1


Keyword Currency  Avg. monthly searches  \
0  create interactive content      ZAR                    0.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                 -1         -1     Unknown                          NaN   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN

The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 3


Keyword Currency  Avg. monthly searches  \
0   interactive content platform      ZAR                    0.0   
1     create interactive content      ZAR                    0.0   
2  interactive content marketing      ZAR                   50.0   

  Three month change YoY change Competition  Competition (indexed value)  \
0                  0         -1     Unknown                          NaN   
1                 -1         -1     Unknown                          NaN   
2                  0          0         Low                          0.0   

   Top of page bid (low range)  Top of page bid (high range)  Avg. Bid Price  \
0                          NaN                           NaN             NaN   
1                          NaN                           NaN             NaN   
2                          NaN                           NaN             NaN   

   Competitiveness Ratio  
0                    NaN  
1                    NaN  
2                    NaN

The number of words that contain "marketing games" is 0


### Discrepencies Between Companies Words Across Countries

#### Creating a dictionaries

Creating a dictionary where the key is the company name and the values are the dataframe of the company in each country 

In [66]:
# Get the names of all dataframes in the global symbol table
all_dataframes = [name for name in globals() if isinstance(globals()[name], pd.DataFrame)]

# Filter dataframes that contain the word "brame"
brame_dataframes = {name: globals()[name] for name in all_dataframes if 'brame' in name}

# # Access and use the filtered dataframes in the dictionary
# for df_name, df in brame_dataframes.items():
#     print(f"DataFrame name: {df_name}")
#     print(df)
#     # Do whatever you need with the dataframe

In [71]:
contains_brame = any('brame' in key for key in dfs.keys())

In [85]:
# Getting the keys that contain 

brame_keys = [key for key in dfs.keys() if 'brame' in key]
playable_keys = [key for key in dfs.keys() if 'playable' in key]
inner_reality_keys = [key for key in dfs.keys() if 'inner_reality' in key]
ceros_keys = [key for key in dfs.keys() if 'ceros' in key]
jebbit_keys = [key for key in dfs.keys() if 'jebbit' in key]
odicci_keys = [key for key in dfs.keys() if 'odicci' in key]

brame = {}
playable = {}
inner_reality = {}
ceros = {}
jebbit = {}
odicci = {}

for key in brame_keys:
    brame[key] = dfs[key]

for key in playable_keys:
    playable[key] = dfs[key]

for key in inner_reality_keys:
    inner_reality[key] = dfs[key]

for key in ceros_keys:
    ceros[key] = dfs[key]

for key in jebbit_keys:
    jebbit[key] = dfs[key]

for key in odicci_keys:
    odicci[key] = dfs[key]

#### Checking discprepancies

In [91]:
for data_frames in brame:   

    print(data_frames)
    company_name = data_frames
    analyze_interesting_keywords(company_name, interesting_keywords, False)

brame_nigera_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 48
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 1
brame_ireland_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 48
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 1
brame_sa_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of wo

In [92]:
for data_frames in playable:   

    print(data_frames)
    company_name = data_frames
    analyze_interesting_keywords(company_name, interesting_keywords, False)


playable_ireland_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 3
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 64
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 10
playable_sa_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 3
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 64
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 10
playable_uk_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 3
The numbe

In [93]:
for data_frames in inner_reality:   

    print(data_frames)
    company_name = data_frames
    analyze_interesting_keywords(company_name, interesting_keywords, False)

inner_reality_nigeria_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 0
inner_reality_ireland_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 0
The number of words that contain "marketing games" is 0
inner_reality_sa_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games

In [94]:
for data_frames in odicci:   

    print(data_frames)
    company_name = data_frames
    analyze_interesting_keywords(company_name, interesting_keywords, False)

odicci_nigeria_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 3
The number of words that contain "marketing games" is 0
odicci_ireland_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of words that contain "create interactive content" is 0
The number of words that contain "gamification" is 0
The number of words that contain "interative advertising" is 0
The number of words that contain "interactive content" is 3
The number of words that contain "marketing games" is 0
odicci_uk_oct
The number of words that contain "advertising games" is 0
The number of words that contain "branded games" is 0
The number of 